In [14]:
import pandas as pd
from besos import eppy_funcs as ef
from besos.evaluator import EvaluatorEP
from besos.parameters import RangeParameter, FieldSelector, FilterSelector, Parameter, expand_plist, wwr, CategoryParameter, GenericSelector
from besos.problem import EPProblem
import numpy as np
import copy
from seaborn import pairplot
import matplotlib.pyplot as plt
HD=0

## Parameters for E+ simulations

In [15]:
nameFile='/home/ict4bd/py3/project/idf_files/triple_on_.idf'
building = ef.get_building(nameFile)

building.idfobjects["Zone"][2].Name[-1]
building.idfobjects["Zone"][0].Name[-1]
building.idfobjects["Zone"][1].Name[-1]


volume_zones=[0,0,0]

volume_zones[int(building.idfobjects["Zone"][0].Name[-1])-1]=building.idfobjects["Zone"][0].Volume
volume_zones[int(building.idfobjects["Zone"][1].Name[-1])-1]=building.idfobjects["Zone"][1].Volume
volume_zones[int(building.idfobjects["Zone"][2].Name[-1])-1]=building.idfobjects["Zone"][2].Volume
volume_zones

[72.9973, 57.2137, 29.1053]

In [16]:
volume_building= sum(volume_zones)

volume_building

159.3163

In [17]:
ACH = range(1,11)
Flow_rate_1= []
Flow_rate_2= []
Flow_rate_3= []
for i in ACH:
    global_Flow_rate = (i * volume_building)/3600
    
    Flow_rate_1.append(global_Flow_rate*volume_zones[0]/volume_building)
    Flow_rate_2.append(global_Flow_rate*volume_zones[1]/volume_building)
    Flow_rate_3.append(global_Flow_rate*volume_zones[2]/volume_building)

    

In [18]:
#here we're building the range within the optimization will happen

building_params= []
orientations = [180,270] #,270
WWRs = [.05, .15, .50] #
thickness = np.linspace(0.0001,0.35,10)
for orientation in orientations:
    for w in WWRs:
        for th in thickness:
            for i in range(len(Flow_rate_1)):
                building_params.append({'Orientation': orientation,
                                             'WWR': w,
                                             'Insulation': th,
                                       'Flow_rate_z1':Flow_rate_1[i],
                                        'Flow_rate_z2':Flow_rate_2[i],
                                        'Flow_rate_z3': Flow_rate_3[i]
                                       })
samples = pd.DataFrame.from_dict(building_params)
samples

Orientation   WWR  Insulation  Flow_rate_z1  Flow_rate_z2  Flow_rate_z3
0            180  0.05      0.0001      0.020277      0.015893      0.008085
1            180  0.05      0.0001      0.040554      0.031785      0.016170
2            180  0.05      0.0001      0.060831      0.047678      0.024254
3            180  0.05      0.0001      0.081108      0.063571      0.032339
4            180  0.05      0.0001      0.101385      0.079463      0.040424
..           ...   ...         ...           ...           ...           ...
595          270  0.50      0.3500      0.121662      0.095356      0.048509
596          270  0.50      0.3500      0.141939      0.111249      0.056594
597          270  0.50      0.3500      0.162216      0.127142      0.064678
598          270  0.50      0.3500      0.182493      0.143034      0.072763
599          270  0.50      0.3500      0.202770      0.158927      0.080848

[600 rows x 6 columns]

## EnergyPlus simulation

In [19]:
results = pd.core.frame.DataFrame()

#extract the building object from the idf file

    #print(building)
#wwr_all(building,0.0001)
# fieldselector()=A selector that modifies one or more fields
#in an EnergyPlus building, based on the class, object and field names   

# Here we change the insulation and orientation of the building
insulation = FieldSelector(class_name='Material', object_name='XPS Extruded Polystyrene  - CO2 Blowing_.O795', field_name='Thickness')
    
orientation = FieldSelector(class_name='Building', field_name='North Axis')

# Setup the parameters
insulationPR = Parameter(selector=insulation, value_descriptor=RangeParameter(0.0001, 0.35),
                             name='Insulation')      
window_to_wall = wwr(CategoryParameter(options=[.05,.15,.5]))

orientationPR = Parameter(selector=orientation, value_descriptor=CategoryParameter(options=[180, 270]),
                          name='Orientation')



zone_1_ventilation = FieldSelector(class_name = 'ZoneVentilation:DesignFlowRate', object_name = 'Blocco1:Zona1 Nat Vent', field_name = 'Design Flow Rate')
zone_1_ventilationPR = Parameter(selector = zone_1_ventilation, value_descriptor=RangeParameter(0.0001,10), name ="Zone 1 Vent")

zone_2_ventilation = FieldSelector(class_name = 'ZoneVentilation:DesignFlowRate', object_name = 'Blocco1:Zona2 Nat Vent', field_name = 'Design Flow Rate')
zone_2_ventilationPR = Parameter(selector = zone_2_ventilation, value_descriptor=RangeParameter(0.0001,10), name ="Zone 2 Vent")

zone_3_ventilation = FieldSelector(class_name = 'ZoneVentilation:DesignFlowRate', object_name = 'Blocco1:Zona3 Nat Vent', field_name = 'Design Flow Rate')
zone_3_ventilationPR = Parameter(selector = zone_3_ventilation, value_descriptor=RangeParameter(0.0001,10), name ="Zone 3 Vent")


/home/ict4bd/py3/lib/python3.8/site-packages/besos-2.1.3-py3.8.egg/besos/parameters.py:424: FutureWarning: Use value_descriptors instead of value_descriptor.
  warnings.warn(
/home/ict4bd/py3/lib/python3.8/site-packages/besos-2.1.3-py3.8.egg/besos/parameters.py:617: UserWarning: wwr is intended to be used with RangeParameter. Your value_descriptor is CategoryParameter(options=[0.05, 0.15, 0.5])
  warnings.warn(


In [20]:

parameters = [orientationPR, window_to_wall, insulationPR,
              zone_1_ventilationPR, zone_2_ventilationPR, zone_3_ventilationPR
             ]

#print(parameters)

objectives = ['Electricity:Facility', 'DistrictHeating:Facility', 'DistrictCooling:Facility']

problem = EPProblem(parameters, objectives)

In [21]:
evaluator = EvaluatorEP(problem, building, out_dir='outputdir_triple_on_', 
                        #error_mode='Silent', 
                        err_dir='outputdir_triple_on_',
                        epw='/home/ict4bd/py3/project/idf_files/GRC_Athens.167160_IWEC.epw')



In [22]:
outputs = evaluator.df_apply(samples, keep_input=True)
#Applies this evaluator to an entire dataFrame, row by row.

 #       :param df: a DataFrame where each row represents valid input values for this Evaluator. 
    #    in this case the inputs are all the possible values of the params to be optimized
       #  :param keep_input: whether to include the input data in the returned DataFrame
      #  :param processes: amount of cores to use (only relevant when using multiprocessing)
       # :param keep_dirs: whether or not keep output directory
        #:return: Returns a DataFrame with one column containing the results for each objective.
        

results = results.append(outputs)
print(results)

Executing:   0%|          | 0/600 [00:00<?, ?row/s]

EnergyPlus Starting
EnergyPlus, Version 9.0.1-bb7ca4f0da, YMD=2021.08.06 10:35
Initializing Response Factors
Calculating CTFs for "PAVIMENTO INTERNO DI PROGETTO", Construction # 3
Calculating CTFs for "TETTO PIANO DI PROGETTO", Construction # 5
Calculating CTFs for "PARTIZIONE DI PROGETTO", Construction # 7
Calculating CTFs for "PARTIZIONE DI PROGETTO_REV", Construction # 8
Calculating CTFs for "PARETE DI PROGETTO", Construction # 9
Initializing Window Optical Properties
Initializing Solar Calculations
Allocate Solar Module Arrays
Initializing Zone Report Variables
Initializing Surface (Shading) Report Variables
Computing Interior Solar Absorption Factors
Determining Shadowing Combinations
Computing Window Shade Absorption Factors
Proceeding with Initializing Solar Calculations
Initializing Surfaces
Initializing Outdoor environment for Surfaces
Setting up Surface Reporting Variables
Initializing Temperature and Flux Histories
Initializing Window Shading
Computing Interior Absorption Fa

EnergyPlus Completed Successfully.


EnergyPlus Starting
EnergyPlus, Version 9.0.1-bb7ca4f0da, YMD=2021.08.06 10:35
Initializing Response Factors
Calculating CTFs for "PAVIMENTO INTERNO DI PROGETTO", Construction # 3
Calculating CTFs for "TETTO PIANO DI PROGETTO", Construction # 5
Calculating CTFs for "PARTIZIONE DI PROGETTO", Construction # 7
Calculating CTFs for "PARTIZIONE DI PROGETTO_REV", Construction # 8
Calculating CTFs for "PARETE DI PROGETTO", Construction # 9
Initializing Window Optical Properties
Initializing Solar Calculations
Allocate Solar Module Arrays
Initializing Zone Report Variables
Initializing Surface (Shading) Report Variables
Computing Interior Solar Absorption Factors
Determining Shadowing Combinations
Computing Window Shade Absorption Factors
Proceeding with Initializing Solar Calculations
Initializing Surfaces
Initializing Outdoor environment for Surfaces
Setting up Surface Reporting Variables
Initializing Temperature and Flux Histories
Initializing Window Shading
Computing Interior Absorption Fa

EnergyPlus Completed Successfully.


...

EnergyPlus Starting
EnergyPlus, Version 9.0.1-bb7ca4f0da, YMD=2021.08.06 14:19
Initializing Response Factors
Calculating CTFs for "PAVIMENTO INTERNO DI PROGETTO", Construction # 3
Calculating CTFs for "TETTO PIANO DI PROGETTO", Construction # 5
Calculating CTFs for "PARTIZIONE DI PROGETTO", Construction # 7
Calculating CTFs for "PARTIZIONE DI PROGETTO_REV", Construction # 8
Calculating CTFs for "PARETE DI PROGETTO", Construction # 9
Initializing Window Optical Properties
Initializing Solar Calculations
Allocate Solar Module Arrays
Initializing Zone Report Variables
Initializing Surface (Shading) Report Variables
Computing Interior Solar Absorption Factors
Determining Shadowing Combinations
Computing Window Shade Absorption Factors
Proceeding with Initializing Solar Calculations
Initializing Surfaces
Initializing Outdoor environment for Surfaces
Setting up Surface Reporting Variables
Initializing Temperature and Flux Histories
Initializing Window Shading
Computing Interior Absorption Fa

EnergyPlus Completed Successfully.


EnergyPlus Starting
EnergyPlus, Version 9.0.1-bb7ca4f0da, YMD=2021.08.06 14:20
Initializing Response Factors
Calculating CTFs for "PAVIMENTO INTERNO DI PROGETTO", Construction # 3
Calculating CTFs for "TETTO PIANO DI PROGETTO", Construction # 5
Calculating CTFs for "PARTIZIONE DI PROGETTO", Construction # 7
Calculating CTFs for "PARTIZIONE DI PROGETTO_REV", Construction # 8
Calculating CTFs for "PARETE DI PROGETTO", Construction # 9
Initializing Window Optical Properties
Initializing Solar Calculations
Allocate Solar Module Arrays
Initializing Zone Report Variables
Initializing Surface (Shading) Report Variables
Computing Interior Solar Absorption Factors
Determining Shadowing Combinations
Computing Window Shade Absorption Factors
Proceeding with Initializing Solar Calculations
Initializing Surfaces
Initializing Outdoor environment for Surfaces
Setting up Surface Reporting Variables
Initializing Temperature and Flux Histories
Initializing Window Shading
Computing Interior Absorption Fa

EnergyPlus Completed Successfully.


     Orientation   WWR  Insulation  Flow_rate_z1  Flow_rate_z2  Flow_rate_z3  \
0            180  0.05      0.0001      0.020277      0.015893      0.008085   
1            180  0.05      0.0001      0.040554      0.031785      0.016170   
2            180  0.05      0.0001      0.060831      0.047678      0.024254   
3            180  0.05      0.0001      0.081108      0.063571      0.032339   
4            180  0.05      0.0001      0.101385      0.079463      0.040424   
..           ...   ...         ...           ...           ...           ...   
595          270  0.50      0.3500      0.121662      0.095356      0.048509   
596          270  0.50      0.3500      0.141939      0.111249      0.056594   
597          270  0.50      0.3500      0.162216      0.127142      0.064678   
598          270  0.50      0.3500      0.182493      0.143034      0.072763   
599          270  0.50      0.3500      0.202770      0.158927      0.080848   

     Electricity:Facility  DistrictHeat

## Consumption

In [23]:
total_area= 0
for Zones in building.idfobjects["Zone"]:
    total_area += float(Zones.checkrange("Floor_Area")) 
total_area

46.8578

In [24]:
#consumption by hour

results['Electricity:Facility'] /= 3.6e6
results['DistrictHeating:Facility'] /= 3.6e6
results['DistrictCooling:Facility'] /= 3.6e6
results['TotalConsumption'] = results['DistrictHeating:Facility'] + results['DistrictCooling:Facility']
results

Orientation   WWR  Insulation  Flow_rate_z1  Flow_rate_z2  Flow_rate_z3  \
0            180  0.05      0.0001      0.020277      0.015893      0.008085   
1            180  0.05      0.0001      0.040554      0.031785      0.016170   
2            180  0.05      0.0001      0.060831      0.047678      0.024254   
3            180  0.05      0.0001      0.081108      0.063571      0.032339   
4            180  0.05      0.0001      0.101385      0.079463      0.040424   
..           ...   ...         ...           ...           ...           ...   
595          270  0.50      0.3500      0.121662      0.095356      0.048509   
596          270  0.50      0.3500      0.141939      0.111249      0.056594   
597          270  0.50      0.3500      0.162216      0.127142      0.064678   
598          270  0.50      0.3500      0.182493      0.143034      0.072763   
599          270  0.50      0.3500      0.202770      0.158927      0.080848   

     Electricity:Facility  DistrictHeating:Facility  DistrictCooling:Facility  \
0             1954.964858               3398.066275               2686.492990   
1             1954.964858               3398.099214               2638.923696   
2             1954.964858               3398.127051               2595.703725   
3             1954.964858               3398.144028               2556.808584   
4             1954.964858               3398.163088               2522.676787   
..                    ...                       ...                       ...   
595           1929.897625               2229.122340               1422.655799   
596           1929.897625               2229.084780               1398.221305   
597           1929.897625               2229.267202               1379.002511   
598           1929.897625               2229.293496               1363.294500   
599           1929.897625               2229.292872               1348.612934   

     TotalConsumption  
0         6084.559265  
1         6037.022910  
2         5993.830776  
3         5954.952612  
4         5920.839875  
..                ...  
595       3651.778139  
596       3627.306085  
597       3608.269713  
598       3592.587997  
599       3577.905806  

[600 rows x 10 columns]

In [25]:
results = results.reset_index()
results

index  Orientation   WWR  Insulation  Flow_rate_z1  Flow_rate_z2  \
0        0          180  0.05      0.0001      0.020277      0.015893   
1        1          180  0.05      0.0001      0.040554      0.031785   
2        2          180  0.05      0.0001      0.060831      0.047678   
3        3          180  0.05      0.0001      0.081108      0.063571   
4        4          180  0.05      0.0001      0.101385      0.079463   
..     ...          ...   ...         ...           ...           ...   
595    595          270  0.50      0.3500      0.121662      0.095356   
596    596          270  0.50      0.3500      0.141939      0.111249   
597    597          270  0.50      0.3500      0.162216      0.127142   
598    598          270  0.50      0.3500      0.182493      0.143034   
599    599          270  0.50      0.3500      0.202770      0.158927   

     Flow_rate_z3  Electricity:Facility  DistrictHeating:Facility  \
0        0.008085           1954.964858               3398.066275   
1        0.016170           1954.964858               3398.099214   
2        0.024254           1954.964858               3398.127051   
3        0.032339           1954.964858               3398.144028   
4        0.040424           1954.964858               3398.163088   
..            ...                   ...                       ...   
595      0.048509           1929.897625               2229.122340   
596      0.056594           1929.897625               2229.084780   
597      0.064678           1929.897625               2229.267202   
598      0.072763           1929.897625               2229.293496   
599      0.080848           1929.897625               2229.292872   

     DistrictCooling:Facility  TotalConsumption  
0                 2686.492990       6084.559265  
1                 2638.923696       6037.022910  
2                 2595.703725       5993.830776  
3                 2556.808584       5954.952612  
4                 2522.676787       5920.839875  
..                        ...               ...  
595               1422.655799       3651.778139  
596               1398.221305       3627.306085  
597               1379.002511       3608.269713  
598               1363.294500       3592.587997  
599               1348.612934       3577.905806  

[600 rows x 11 columns]

In [26]:
#hourly consumption by squared meter
results['Electricity:Facility'] /= total_area
results['DistrictHeating:Facility'] /= total_area
results['DistrictCooling:Facility'] /= total_area
results['TotalConsumption'] /= total_area
results

index  Orientation   WWR  Insulation  Flow_rate_z1  Flow_rate_z2  \
0        0          180  0.05      0.0001      0.020277      0.015893   
1        1          180  0.05      0.0001      0.040554      0.031785   
2        2          180  0.05      0.0001      0.060831      0.047678   
3        3          180  0.05      0.0001      0.081108      0.063571   
4        4          180  0.05      0.0001      0.101385      0.079463   
..     ...          ...   ...         ...           ...           ...   
595    595          270  0.50      0.3500      0.121662      0.095356   
596    596          270  0.50      0.3500      0.141939      0.111249   
597    597          270  0.50      0.3500      0.162216      0.127142   
598    598          270  0.50      0.3500      0.182493      0.143034   
599    599          270  0.50      0.3500      0.202770      0.158927   

     Flow_rate_z3  Electricity:Facility  DistrictHeating:Facility  \
0        0.008085             41.721226                 72.518690   
1        0.016170             41.721226                 72.519393   
2        0.024254             41.721226                 72.519987   
3        0.032339             41.721226                 72.520349   
4        0.040424             41.721226                 72.520756   
..            ...                   ...                       ...   
595      0.048509             41.186262                 47.572066   
596      0.056594             41.186262                 47.571264   
597      0.064678             41.186262                 47.575157   
598      0.072763             41.186262                 47.575718   
599      0.080848             41.186262                 47.575705   

     DistrictCooling:Facility  TotalConsumption  
0                   57.332888        129.851578  
1                   56.317704        128.837097  
2                   55.395339        127.915326  
3                   54.565272        127.085621  
4                   53.836859        126.357615  
..                        ...               ...  
595                 30.361131         77.933197  
596                 29.839670         77.410934  
597                 29.429519         77.004676  
598                 29.094292         76.670010  
599                 28.780970         76.356675  

[600 rows x 11 columns]

## Find best settings (i.e. minimizing consumption)

In [27]:
# Best settings
min_value_index = results[['TotalConsumption']].idxmin()
print(results.iloc[min_value_index])
#DECIDE PLOTS TO PUT IN REPORT

    index  Orientation   WWR  Insulation  Flow_rate_z1  Flow_rate_z2  \
99     99          180  0.05        0.35       0.20277      0.158927   

    Flow_rate_z3  Electricity:Facility  DistrictHeating:Facility  \
99      0.080848             41.721226                 48.024119   

    DistrictCooling:Facility  TotalConsumption  
99                 24.864884         72.889003  


In [28]:
results["name"]=nameFile.split("/")[-1]

if HD==0:
    results.iloc[min_value_index].to_csv('opt_results.csv', mode='a', header=True)
else:
    results.iloc[min_value_index].to_csv('opt_results.csv', mode='a', header=False)

HD=1